In [ ]:
# Imports
import folium
import branca
import requests
import json
import base64
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from folium import IFrame


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
# PART 1
arrest_table = pd.read_csv("https://cmsc320.github.io/files/BPD_Arrests.csv")

arrest_table = arrest_table[pd.notnull(arrest_table["Location 1"])]

arrest_table["lat"], arrest_table["long"] = arrest_table["Location 1"].str.split(",").str
arrest_table["lat"] = arrest_table["lat"].str.replace("(", "").astype(float)
arrest_table["long"] = arrest_table["long"].str.replace(")", "").astype(float)
arrest_table.head()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:6: FutureWarning: Columnar iteration over characters will be deprecated in future releases.
  


arrest  age race  ...                       Location 1        lat       long
1  11127013.0   37    B  ...  (39.2814026274, -76.6483635135)  39.281403 -76.648364
2  11126887.0   46    B  ...  (39.3227699160, -76.5735750473)  39.322770 -76.573575
3  11126873.0   50    B  ...  (39.3117196723, -76.6623546313)  39.311720 -76.662355
4  11126968.0   33    B  ...  (39.3382885254, -76.6045667070)  39.338289 -76.604567
5  11127041.0   41    B  ...  (39.2449886230, -76.6273582432)  39.244989 -76.627358

[5 rows x 17 columns]

In [ ]:
# PART 2
map_osm = folium.Map(location=[39.29, -76.61], zoom_start=13)

In [ ]:
# PART 3

# This interactive map will convey each neighborhood's relative frequency of
# arrests via a choropleth. There will also be clickable icons for each
# neighborhood to see how the arrests vary by race

# We will make a new dataframe for statistics in each neighborhood
nbh_table = pd.DataFrame()

# Drop rows where neighborhood is missing
tmp = arrest_table[arrest_table['neighborhood'].notna()]

# Get all neighborhood names
neighborhoods = tmp.neighborhood.unique()
neighborhoods.sort()
neighborhoods = list(map(str,neighborhoods))

# Count frequency of arrests in each neighborhood
freq = arrest_table.groupby(['neighborhood']).size()

# Make columns
nbh_table['neighborhood'] = neighborhoods
nbh_table['arrests'] = freq.array

# Calculate relative frequencies
s = sum(nbh_table['arrests'])
nbh_table['percent'] = list(map(lambda x: round(100*(x/s),3),nbh_table['arrests']))

nbh_table

neighborhood  arrests  percent
0                Abell       62    0.097
1            Allendale      297    0.466
2              Arcadia       78    0.122
3            Arlington      694    1.088
4    Armistead Gardens      153    0.240
..                 ...      ...      ...
262           Woodmere      559    0.876
263           Woodring       70    0.110
264         Wyman Park        5    0.008
265          Wyndhurst        2    0.003
266       Yale Heights       81    0.127

[267 rows x 3 columns]

In [ ]:
# Create Bar Plots:

for i,n in enumerate(neighborhoods):
    tmp2 = tmp[tmp['neighborhood']==n]
    races = ['B','W','A','I','U','H']

    # store data for this neighborhood in a dictionary
    data = dict.fromkeys(races, 0)
    for r in races:
      # Count number of occurences of specified race
      data[r] = len(tmp2[tmp2['race']==r])

    # Create plot
    fig,ax = plt.subplots()
    ax.bar(data.keys(), data.values())
    ax.set_title("Arrests by Race in " + str(n))
    plt.close(fig)

    # Save plot as image, labelled by the neighborhood's index
    fig.savefig(f"{i}.png")

# (This takes a while!)

In [ ]:
# Find average arrest location in each neighborhood
# This is where the marker for each neighborhood will go

avg_lon = []
avg_lat = []

for n in neighborhoods:
  tmp2 = tmp[tmp['neighborhood']==n]
  lons = list(tmp2['long'])
  lats = list(tmp2['lat'])
  avg_lon.append(sum(lons)/float(len(lons)))
  avg_lat.append(sum(lats)/float(len(lats)))

In [ ]:
# Add these coordinates to dataframe
nbh_table['avg_long'] = avg_lon
nbh_table['avg_lat'] = avg_lat
nbh_table

neighborhood  arrests  percent   avg_long    avg_lat
0                Abell       62    0.097 -76.610109  39.326355
1            Allendale      297    0.466 -76.677655  39.291359
2              Arcadia       78    0.122 -76.566235  39.330275
3            Arlington      694    1.088 -76.681051  39.347303
4    Armistead Gardens      153    0.240 -76.550246  39.304502
..                 ...      ...      ...        ...        ...
262           Woodmere      559    0.876 -76.686572  39.345199
263           Woodring       70    0.110 -76.546114  39.362987
264         Wyman Park        5    0.008 -76.626715  39.329594
265          Wyndhurst        2    0.003 -76.623836  39.354542
266       Yale Heights       81    0.127 -76.690647  39.276742

[267 rows x 5 columns]

In [ ]:
# Place Markers on the Map

# Special thanks to StackOverflow

for i,row in nbh_table.iterrows():
  # Get image of barplot for this neighborhood
  encoded = base64.b64encode(open(f"{i}.png", 'rb').read())

  # Formatting
  html = '<img src="data:image/png;base64,{}">'.format
  iframe = IFrame(html(encoded.decode('UTF-8')), width=400, height=350)

  # Attatch image to a popup for this marker
  popup = folium.Popup(iframe, max_width=450)

  # Place marker
  folium.Marker(location=[row['avg_lat'], row['avg_long']], tooltip=html, popup=popup,
  icon=folium.Icon(color='grey')).add_to(map_osm)

In [ ]:
# To make the choropleth, we will be using a set of geoJSON data found online

url = "https://raw.githubusercontent.com/blackmad/neighborhoods/master/baltimore.geojson"
geo = json.loads(requests.get(f"{url}").text)

Due to some discrepencies between the given data and the geoJson data, our\
dataframe needs to change some names and make some new rows so the\
choropleth does not have as many black spots. The following changes are made:

Washiongton Village -> Washington Village/Pigtown\
Booth-Boyd -> Boyd-Booth\
SBIC -> South Baltimore\
Baltimore-Linewood -> Patterson Park Neighborhood\
Jospeh Lee -> Part of Bayview\
Claremont-Freedom -> Orchard Ridge\
Glenham-Belford -> Glenham-Belhar\
Harford-Echodale/Perring Parkway + Christopher -> Hamilton Hills\
Edmondson Village -> extend to Edgewood and Lower Edmondson\
Lake Evesham -> extend to Evesham Park\
Chinquapin Park-Belvedere -> split into Chinquapin Park and Belvedere

In [ ]:
# Renaming Neighborhoods
nbh_table.replace(to_replace='Washington Village', value='Washington Village/Pigtown', inplace=True)
nbh_table.replace(to_replace='Booth-Boyd', value='Boyd-Booth', inplace=True)
nbh_table.replace(to_replace='SBIC', value='South Baltimore', inplace=True)
nbh_table.replace(to_replace='Baltimore-Linwood', value='Patterson Park Neighborhood', inplace=True)
nbh_table.replace(to_replace='Joseph Lee', value='Bayview', inplace=True)
nbh_table.replace(to_replace='Claremont-Freedom', value='Orchard Ridge', inplace=True)
nbh_table.replace(to_replace='Glenham-Belford', value='Glenham-Belhar', inplace=True)

# Merging Harford-Echodale/Perring Parkway and Christopher into Hamilton Hills
tmp2 = nbh_table[nbh_table['neighborhood'].isin(['Harford-Echodale/Perring Parkway','Christopher'])]
p = (float(sum(list(tmp2['percent']))))/2.0
new_row = {'neighborhood':'Hamilton Hills', 'arrests':0, 'percent':p, 'avg_long':0, 'avg_lat':0}
nbh_table = nbh_table.append(new_row, ignore_index=True)

# Extending Edmondson Village to Lower Edmondson, and Edgwood
tmp2 = nbh_table[nbh_table['neighborhood']=='Edmondson Village']
new_row = {'neighborhood':'Edgewood', 'arrests':0, 'percent':sum(tmp2['percent']), 'avg_long':0, 'avg_lat':0}
nbh_table = nbh_table.append(new_row, ignore_index=True)
new_row = {'neighborhood':'Lower Edmondson Village', 'arrests':0, 'percent':sum(tmp2['percent']), 'avg_long':0, 'avg_lat':0}
nbh_table = nbh_table.append(new_row, ignore_index=True)

# Extending Lake Evesham to Evesham Park
tmp2 = nbh_table[nbh_table['neighborhood']=='Lake Evesham']
new_row = {'neighborhood':'Evesham Park', 'arrests':0, 'percent':sum(tmp2['percent']), 'avg_long':0, 'avg_lat':0}
nbh_table = nbh_table.append(new_row, ignore_index=True)

# Extending Downtown to Downtown West
tmp2 = nbh_table[nbh_table['neighborhood']=='Downtown']
new_row = {'neighborhood':'Downtown West', 'arrests':0, 'percent':sum(tmp2['percent']), 'avg_long':0, 'avg_lat':0}
nbh_table = nbh_table.append(new_row, ignore_index=True)

# Splitting Chinquapin Park-Belvedere into Chinquapin Park and Belvedere
tmp2 = nbh_table[nbh_table['neighborhood']=='Chinquapin Park-Belvedere']
new_row = {'neighborhood':'Chinquapin Park', 'arrests':0, 'percent':sum(tmp2['percent']), 'avg_long':0, 'avg_lat':0}
nbh_table = nbh_table.append(new_row, ignore_index=True)
new_row = {'neighborhood':'Belvedere', 'arrests':0, 'percent':sum(tmp2['percent']), 'avg_long':0, 'avg_lat':0}
nbh_table = nbh_table.append(new_row, ignore_index=True)


In [ ]:
# Create Choropleth

choropleth = folium.Choropleth(
    geo_data=geo,
    name="choropleth",
    data=nbh_table,
    columns=['neighborhood', 'percent'],
    key_on="feature.properties.name",
    fill_color="Reds",
    fill_opacity=0.75,
    line_opacity=1,
    legend_name="Arrest Rate (%)",
    bins=[0, 1, 5, 10, 20, 50],
    reset=True
).add_to(map_osm)

In [ ]:
# Add a tooltip
# This makes it easier to see the neighborhood name without having to click the marker

folium.LayerControl().add_to(map_osm)
style_function = "font-size: 15px; font-weight: bold"
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['name'], style=style_function, labels=False))
folium.LayerControl().add_to(map_osm)

This map gives an idea of where arrests most often occur. The redder\
neighborhoods contribute more to the total amount of Baltimore arrests.\
The yellower areas contribute far less. Neighborhoods colored black are\
considered to have "no data," because their names were both excluded from the\
dataset and have no clear synonymous names. Hover the mouse over a\
neighborhood to see its name.

The markers in each neighborhood represent the average coordinates of where\
arrests occur within that neighborhood. The location of these markers are not\
all too meaningful. They are meant to be an approximate center of the\
neighborhood for placing makers, although this does not work well for some.\
Click on a marker to see a barplot with the racial breakdown of arrests.

In [ ]:
# (This may take some time)
map_osm